# Coleta e Carga

Neste trabalho utilizaremos uma abordagem ELTL(Extract-Load-Transform-Load), onde os dados de interesse serão primeiro extraídos e carregados crus, depois faremos dois modelos derivados deste, um com dados granulares e outro agregado.

Todos os dados crus que iremos utilizar neste trabalho são dados públicos, sem qq restrição de uso e sem dados pessoais envolvidos.

## 1 - QSA / RFB

Iremos utilizar como ponto de partida para a resolução das questões postas a base pública de dados de empresas (CNPJ, QSA) da RFB, porque é a base que contém os dados oficiais de empresas, de onde podemos fazer uma pesquisa de mercado mais fidedigna possível.

Os dados da base estão disponíveis como arquivos zip em pastas no endereço base abaixo:
https://arquivos.receitafederal.gov.br/dados/cnpj/dados_abertos_cnpj/

Os dados mais recentes disponíveis quando da realização deste trabalho são os de fev/2025, disponíveis em:

https://arquivos.receitafederal.gov.br/dados/cnpj/dados_abertos_cnpj/2025-02/

Estaremos baixando os dados de Empresas, Estabelecimentos e as tabelas de domínio de CNAEs, Municípios, Motivos de Situação e Natureza Jurídica.

IMPORTANTE:
- Esta é uma base GRANDE, com mais de 15 milhões de empresas ativas cadastradas e mais de 16 GB de tamanho. Vamos tentar baixar todos os dados e carregar no Spark
- Apesar de não dizer claramente na sua doc, é possível constatar que os arquivos da RFB vem em encoding ISO-8859-1. É importante no processamento dos arquivos no Spark utilizar este encoding correto na leitura e persistência dos dados

### Coleta / Extração (geral)

O processamento no Databricks Community Edition parece ser limitado a 1 h. Como baixar os arquivos, dezipar e processar no Spark dentro da plataforma estava levando muito tempo, não foi possível fazer tudo dentro da plataforma.

A solução encontrada foi baixar os arquivos offline no meu computador pessoal, dezipar os arquivos localmente e subí-los para um bucket S3 (no caso do Tigris (https://www.tigrisdata.com/), que parece ser mais barato que o S3 da AWS) e de lá ler no Spark do Databricks e salvar em uma Spark Table.

In [0]:
# instalar libs necessárias:
# dotenv -> para leitura de variáveis de ambiente, para não deixar secrets explícitos no código
# boto3 -> para interação com storages S3-like 

!pip install dotenv
!pip install boto3

  Using cached dotenv-0.9.9-py2.py3-none-any.whl (1.9 kB)
  Using cached python_dotenv-1.0.1-py3-none-any.whl (19 kB)
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-e2138243-6b66-4d28-a44d-6b03143ea468/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-e2138243-6b66-4d28-a44d-6b03143ea468/bin/python -m pip install --upgrade pip' command.


In [0]:
# copiando arquivo .env do dbfs para o dir local, para que a lib dotenv consiga ler
dbutils.fs.cp("dbfs:/FileStore/.env", "file:/tmp/env/", True) 

Out[2]: True

In [0]:
# configurações preliminares

import os
import gc
from pyspark.sql import SparkSession
from dotenv import load_dotenv

load_dotenv(dotenv_path="/tmp/env") # ler arquivo .env do dir local
print("Variáveis de ambiente carregadas")

Variáveis de ambiente carregadas


In [0]:
# configuração geral do Spark

spark = SparkSession.builder.appName("CargaMVP") \
    .getOrCreate()

# setar variáveis para acessar o Tigris
spark.sparkContext._jsc.hadoopConfiguration().set("fs.s3a.endpoint", os.getenv("AWS_ENDPOINT_URL_S3"))
spark.sparkContext._jsc.hadoopConfiguration().set("fs.s3a.access.key", os.getenv("AWS_ACCESS_KEY_ID"))
spark.sparkContext._jsc.hadoopConfiguration().set("fs.s3a.secret.key", os.getenv("AWS_SECRET_ACCESS_KEY"))
spark.sparkContext._jsc.hadoopConfiguration().set("fs.s3a.path.style.access", "true")
spark.sparkContext._jsc.hadoopConfiguration().set("fs.s3a.connection.ssl.enabled", "true")



### 1.1 - Dados de Empresas (CNPJ raiz, 8 dígitos)

#### Carga

In [0]:

# path S3 no Tigris onde estão os dados de Empresas
s3_dir = "s3a://pos-pucrio-dados/mvp_sprint_eng_dados/emp/"

# os arquivos da RFB estão vindo sem header - ler primeiro sem headers e acrescentar na mão depois
# OBS: infelizmente, em alguns dos registros há um caracter '\' no nome da empresa escapando indevidamente as aspas duplas ('"') do fim da razao social... mudar caracter de escape para '"'
df_sem_headers = spark.read.option("delimiter", ";").option("escape", "\"").option("multiLine", True).option("encoding", "iso-8859-1").csv(s3_dir, header=False, inferSchema=True) 

# headers segundo doc (https://www.gov.br/receitafederal/dados/cnpj-metadados.pdf)
headers = ["cnpj_raiz", "razao_social", "natureza_jur", "qualificacao_resp", "capital_soc", "porte", "ente_fed_resp"]

#df_sem_headers.show()
df = df_sem_headers.toDF(*headers) # acrescenta os headers no df original

In [0]:
# finalmente, carrega os dados em uma tabela Spark
df.write.option("encoding", "iso-8859-1").option("overwriteSchema", "true").mode("overwrite").saveAsTable("empresas")

In [0]:
%sql
select * from empresas where cnpj_raiz = 2209756

cnpj_raiz razao_social natureza_jur qualificacao_resp capital_soc porte ente_fed_resp 2209756 SOLANGE DA S.LEITE GOES\ 2135 50 0,00 5 null

In [0]:
%sql
-- verificando que inseriu corretamente, fazer select simples
select porte, count(distinct cnpj_raiz) from empresas group by porte

porte count(DISTINCT cnpj_raiz) null 71850 1 45171542 3 1772439 5 14464944

In [0]:
# apagar dfs sem uso, liberar memória
del df
del df_sem_headers
gc.collect()

Out[9]: 477

### 1.2 - Dados de Estabelecimentos (CNPJ full, 11 dígitos)

#### Carga

In [0]:

# path S3 no Tigris onde estão os dados de Empresas
s3_dir = "s3a://pos-pucrio-dados/mvp_sprint_eng_dados/estab/"

# os arquivos da RFB estão vindo sem header - ler primeiro sem headers e acrescentar na mão depois
# OBS: infelizmente, em alguns dos registros há um caracter '\' no nome da empresa escapando indevidamente as aspas duplas ('"') do fim da razao social... mudar caracter de escape para '"'
df_sem_headers = spark.read.option("delimiter", ";").option("escape", "\"").option("multiLine", True).option("encoding", "iso-8859-1").csv(s3_dir, header=False, inferSchema=True) 

# headers segundo doc (https://www.gov.br/receitafederal/dados/cnpj-metadados.pdf)
headers = ["cnpj_raiz", "cnpj_ordem", "cnpj_dv", "ind_matriz_filial", "nome_fantasia", "situacao", "dat_situacao", "mot_situacao", "cidade_exterior", "pais", "dat_inicio_atividade", "CNAE_principal", "CNAEs_secundarios", "tip_logradouro", "logradouro", "num_logradouro", "compl_logradouro", "bairro", "CEP", "UF", "municipio", "ddd1", "tel1", "ddd2", "tel2", "ddd_fax", "fax", "email", "sit_especial", "dat_sit_especial"]

#df_sem_headers.show()
df = df_sem_headers.toDF(*headers) # acrescenta os headers no df original

In [0]:
# finalmente, carrega os dados em uma tabela Spark
df.write.option("encoding", "iso-8859-1").option("overwriteSchema", "true").mode("overwrite").saveAsTable("estabelecimentos")

In [0]:
%sql
select * from estabelecimentos where cnpj_raiz = "28645283"

cnpj_raiz cnpj_ordem cnpj_dv ind_matriz_filial nome_fantasia situacao dat_situacao mot_situacao cidade_exterior pais dat_inicio_atividade CNAE_principal CNAEs_secundarios tip_logradouro logradouro num_logradouro compl_logradouro bairro CEP UF municipio ddd1 tel1 ddd2 tel2 ddd_fax fax email sit_especial dat_sit_especial 28645283 1 48 1 "MAIZE AKISOPA"ALIMENTOS DOCES E SAGADOS ;DIET & LIGHT 8 20171202 1 null null 20170914 5620104 1091102 RUA DO IRERE 158 APT BANGU 21875230 RJ 6001 21 39029277 null null null null dearaujosilvamariajose@yahoo.com.br null null

In [0]:
%sql
-- verificando que inseriu corretamente, fazer select simples
select CNAE_principal, count(concat(cnpj_raiz, cnpj_ordem, cnpj_dv) ) from estabelecimentos group by CNAE_principal

CNAE_principal count(concat(cnpj_raiz, cnpj_ordem, cnpj_dv)) 113000 191761 4322301 71801 7733100 10743 1041400 1633 8730199 7383 9602502 643801 7739099 53718 8690901 24879 4399199 56001 3839499 15498 2052500 2007 119907 329 6432800 267 2449103 85 4789005 109368 1042200 578 321305 129 2122000 910 1722200 204 4329101 20255 7810800 71961 4689399 46121 9003500 1979 4291000 4771 2424501 491 8690902 19 1111901 7073 1099605 2493 1061901 7912 5022001 834 4729602 25107 7732202 5225 4929903 4002 2610800 4793 2221800 2068 3250705 2245 112101 1747 6611804 50 3900500 456 5022002 1033 4724500 270902 5620102 120252 133404 11113 6311900 65314 6110802 361 6612604 1718 4649406 1299 4671100 30733 3314705 1014 4681803 3793 133499 8227 1012104 45 5130700 37 892402 17 4930201 867506 4729601 196258 8292000 13050 8711504 512 220902 1538 5821200 5485 1210700 141 7990200 21664 139399 3045 2930101 4290 4681801 9639 5310501 9888 220905 109 5620103 33543 8650003 95082 3832700 18740 4512901 7876 119909 5603 1020102 2076 8299707 39780 3250706 10801 153902 1573 9200399 1196 4683400 23309 2740601 295 3103900 13069 8640207 6284 3600602 6737 4644301 21752 810099 5988 2812700 1592 1011205 1340 3240003 307 5012202 52 7911200 200936 9609206 61034 4543900 87128 4652400 7160 3314710 21330 119999 16552 8592999 123608 7119703 22578 4641902 3256 6822600 56423 4744005 152060 7723300 42491 6611801 94 2823200 3973 2821602 310 4929999 2621 2550102 108 4723700 822505 2093200 1978 4632002 3856 4673700 8103 155502 981 4643501 9593 1220402 176 5091202 2299 112199 838 133401 549 2910701 541 1220401 1037 1099699 15593 4634601 18403 8542200 1260 4649410 6362 1922599 329 6622300 113676 8211300 431496 5099899 4786 4651602 1638 162899 11263 5310502 6844 6423900 6546 1340502 776 3041500 437 2073800 662 9601701 56291 2399101 21768 210103 3197 5011401 2416 2121103 156 3312104 1024 8299704 946 6450600 915 4940000 390 5240101 1322 810001 11872 4912401 192 6422100 45001 5099801 6322 3011302 906 133403 217 2099101 190 2439300 458 4782202 30495 1531901 44467 4632003 5606 3211602 7444 4751200 31 4789002 88131 4744002 68384 4299599 22594 4664800 4899 4713005 367 4632001 30738 4530702 5410 2942500 360 6431000 302 119901 1810 899103 8 600001 1961 1311100 2656 7120100 10102 1312000 1539 6141800 1146 729401 756 4711302 123668 8640202 45067 1122403 1408 2071100 5393 9001905 1580 1323500 1352 4911600 550 5021101 3256 4649402 8676 9529105 45204 1413402 3939 210105 502 4511105 536 2449199 1506 1610203 46701 3299005 2624 4649404 5252 4511102 103880 810007 2327 9329801 10159 2840200 3564 2864000 940 6319400 46246 1932200 451 119906 8767 6810203 17425 4789008 33853 8622400 1750 4645102 951 1811302 5513 3316302 299 8421300 290 161003 103442 6399200 33816 3319800 16872 4612500 19457 4329104 8801 9102302 2467 5222200 4243 1011203 190 1910100 89 151201 227914 8630599 39185 3512300 2958 8640204 2443 1093702 4975 1099601 8045 7490102 2368 4753900 237007 5611204 440470 111302 52741 2950600 11731 6010100 19868 8030700 6569 9200301 17238 8599604 516662 4322302 168079 4929902 86312 4649401 67704 8299701 1988 3250701 1525 1065101 2192 4649407 1316 5211799 12531 4679699 19018 4542101 3296 8621601 1220 1532700 1491 139306 42905 2511000 21184 4689302 10880 2072000 250 810009 1147 7729203 1473 7912100 26033 3292202 5159 2622100 1647 3314719 9213 8650099 26127 4771704 38695 5510803 8558 2442300 532 4221905 4954 8640203 1760 311602 517 9609202 21583 4642701 53148 4693100 57536 3812200 2161 1069400 6699 3012100 1577 111399 2625 6530800 146 312404 275 2815101 63 2670102 128 133411 340 8599699 577761 4761002 27767 5510801 90999 9603304 23354 9603399 2679 4682600 2980 4511106 203 9200302 263 2824101 103 3314799 17314 1540800 9077 3314713 4258 9609207 16364 8650006 21999 9321200 3000 4292801 17780 1063500 6682 5913800 6500 8640209 1628 1931400 1919 3250704 155 1099602 503 8599605 65414 4617600 79548 4763601 92164 7711000 63828 5590603 22932 6190601 15760 6492100 3289 5911101 4730 1741902 3196 8130300 230782 5590699 49873 773

In [0]:
# apagar dfs sem uso, liberar memória
del df
del df_sem_headers
gc.collect()

Out[14]: 485

### 1.3 - Dados de CNAEs

#### Carga

In [0]:

# path S3 no Tigris onde estão os dados de Empresas
s3_dir = "s3a://pos-pucrio-dados/mvp_sprint_eng_dados/cnae/"

# os arquivos da RFB estão vindo sem header
# ler primeiro sem headers e acrescentar na mão depois
df_sem_headers = spark.read.option("delimiter", ";").option("encoding", "iso-8859-1").csv(s3_dir, header=False, inferSchema=True) 

# headers segundo doc (https://www.gov.br/receitafederal/dados/cnpj-metadados.pdf)
headers = ["codigo", "descricao"]

#df_sem_headers.show()
df = df_sem_headers.toDF(*headers) # acrescenta os headers no df original

In [0]:
# finalmente, carrega os dados em uma tabela Spark
df.write.option("encoding", "iso-8859-1").option("overwriteSchema", "true").mode("overwrite").saveAsTable("cnae")

In [0]:
%sql
-- verificando que inseriu corretamente, fazer select simples
select * from cnae

codigo descricao 111301 Cultivo de arroz 111302 Cultivo de milho 111303 Cultivo de trigo 111399 Cultivo de outros cereais não especificados anteriormente 112101 Cultivo de algodão herbáceo 112102 Cultivo de juta 112199 Cultivo de outras fibras de lavoura temporária não especificadas anteriormente 113000 Cultivo de cana-de-açúcar 114800 Cultivo de fumo 115600 Cultivo de soja 116401 Cultivo de amendoim 116402 Cultivo de girassol 116403 Cultivo de mamona 116499 Cultivo de outras oleaginosas de lavoura temporária não especificadas anteriormente 119901 Cultivo de abacaxi 119902 Cultivo de alho 119903 Cultivo de batata-inglesa 119904 Cultivo de cebola 119905 Cultivo de feijão 119906 Cultivo de mandioca 119907 Cultivo de melão 119908 Cultivo de melancia 119909 Cultivo de tomate rasteiro 119999 Cultivo de outras plantas de lavoura temporária não especificadas anteriormente 121101 Horticultura, exceto morango 121102 Cultivo de morango 122900 Cultivo de flores e plantas ornamentais 131800 Cultivo de laranja 132600 Cultivo de uva 133401 Cultivo de açaí 133402 Cultivo de banana 133403 Cultivo de caju 133404 Cultivo de cítricos, exceto laranja 133405 Cultivo de coco-da-baía 133406 Cultivo de guaraná 133407 Cultivo de maçã 133408 Cultivo de mamão 133409 Cultivo de maracujá 133410 Cultivo de manga 133411 Cultivo de pêssego 133499 Cultivo de frutas de lavoura permanente não especificadas anteriormente 134200 Cultivo de café 135100 Cultivo de cacau 139301 Cultivo de chá-da-índia 139302 Cultivo de erva-mate 139303 Cultivo de pimenta-do-reino 139304 Cultivo de plantas para condimento, exceto pimenta-do-reino 139305 Cultivo de dendê 139306 Cultivo de seringueira 139399 Cultivo de outras plantas de lavoura permanente não especificadas anteriormente 141501 Produção de sementes certificadas, exceto de forrageiras para pasto 141502 Produção de sementes certificadas de forrageiras para formação de pasto 142300 Produção de mudas e outras formas de propagação vegetal, certificadas 151201 Criação de bovinos para corte 151202 Criação de bovinos para leite 151203 Criação de bovinos, exceto para corte e leite 152101 Criação de bufalinos 152102 Criação de eqüinos 152103 Criação de asininos e muares 153901 Criação de caprinos 153902 Criação de ovinos, inclusive para produção de lã 154700 Criação de suínos 155501 Criação de frangos para corte 155502 Produção de pintos de um dia 155503 Criação de outros galináceos, exceto para corte 155504 Criação de aves, exceto galináceos 155505 Produção de ovos 159801 Apicultura 159802 Criação de animais de estimação 159803 Criação de escargô 159804 Criação de bicho-da-seda 159899 Criação de outros animais não especificados anteriormente 161001 Serviço de pulverização e controle de pragas agrícolas 161002 Serviço de poda de árvores para lavouras 161003 Serviço de preparação de terreno, cultivo e colheita 161099 Atividades de apoio à agricultura não especificadas anteriormente 162801 Serviço de inseminação artificial em animais 162802 Serviço de tosquiamento de ovinos 162803 Serviço de manejo de animais 162899 Atividades de apoio à pecuária não especificadas anteriormente 163600 Atividades de pós-colheita 170900 Caça e serviços relacionados 210101 Cultivo de eucalipto 210102 Cultivo de acácia-negra 210103 Cultivo de pinus 210104 Cultivo de teca 210105 Cultivo de espécies madeireiras, exceto eucalipto, acácia-negra, pinus e teca 210106 Cultivo de mudas em viveiros florestais 210107 Extração de madeira em florestas plantadas 210108 Produção de carvão vegetal - florestas plantadas 210109 Produção de casca de acácia-negra - florestas plantadas 210199 Produção de produtos não-madeireiros não especificados anteriormente em florestas plantadas 220901 Extração de madeira em florestas nativas 220902 Produção de carvão vegetal - florestas nativas 220903 Coleta de castanha-do-pará em florestas nativas 220904 Coleta de látex em florestas nativas 220905 Coleta de palmito em florestas nativas 220906 Conservação de florestas nativas 220999 

### 1.4 - Dados de Municípios

#### Carga

In [0]:

# path S3 no Tigris onde estão os dados de Empresas
s3_dir = "s3a://pos-pucrio-dados/mvp_sprint_eng_dados/mun/"

# os arquivos da RFB estão vindo sem header
# ler primeiro sem headers e acrescentar na mão depois
df_sem_headers = spark.read.option("delimiter", ";").option("encoding", "iso-8859-1").csv(s3_dir, header=False, inferSchema=True) 

# headers segundo doc (https://www.gov.br/receitafederal/dados/cnpj-metadados.pdf)
headers = ["codigo", "descricao"]

#df_sem_headers.show()
df = df_sem_headers.toDF(*headers) # acrescenta os headers no df original

In [0]:
# finalmente, carrega os dados em uma tabela Spark
df.write.option("encoding", "iso-8859-1").option("overwriteSchema", "true").mode("overwrite").saveAsTable("municipio")

In [0]:
%sql
-- verificando que inseriu corretamente, fazer select simples
select * from municipio

codigo descricao 1 GUAJARA-MIRIM 2 ALTO ALEGRE DOS PARECIS 3 PORTO VELHO 4 BURITIS 5 JI-PARANA 6 CHUPINGUAIA 7 ARIQUEMES 8 CUJUBIM 9 CACOAL 10 NOVA UNIAO 11 PIMENTA BUENO 12 PARECIS 13 VILHENA 14 PIMENTEIRAS DO OESTE 15 JARU 16 PRIMAVERA DE RONDONIA 17 OURO PRETO DO OESTE 18 SAO FELIPE D'OESTE 19 PRESIDENTE MEDICI 20 SAO FRANCISCO DO GUAPORE 21 COSTA MARQUES 22 TEIXEIROPOLIS 23 COLORADO DO OESTE 24 VALE DO ANARI 25 ESPIGAO D'OESTE 26 AMAJARI 27 CEREJEIRAS 28 CANTA 29 ROLIM DE MOURA 30 CAROEBE 31 CALDAZINHA 32 IRACEMA 33 ALTA FLORESTA D'OESTE 34 PACARAIMA 35 ALVORADA D'OESTE 36 RORAINOPOLIS 37 CABIXI 38 UIRAMUTA 39 MACHADINHO D'OESTE 40 ANAPU 41 NOVA BRASILANDIA D'OESTE 42 BANNACH 43 SANTA LUZIA D'OESTE 44 BELTERRA 45 SAO MIGUEL DO GUAPORE 46 CACHOEIRA DO PIRIA 47 NOVA MAMORE 48 CANAA DOS CARAJAS 49 JESUPOLIS 50 CURUA 51 PROFESSOR JAMIL 52 FLORESTA DO ARAGUAIA 53 SANTO ANTONIO DE GOIAS 54 MARITUBA 55 COCALZINHO DE GOIAS 56 NOVA IPIXUNA 57 TEREZOPOLIS DE GOIAS 58 PICARRA 59 UIRAPURU 60 PLACAS 61 BURITINOPOLIS 62 QUATIPURU 63 BURITI DE GOIAS 64 SAO JOAO DA PONTA 65 GUARAITA 66 SAPUCAIA 67 VILA BOA 68 TRACUATEUA 69 INACIOLANDIA 70 VITORIA DO JARI 71 APARECIDA DO RIO DOCE 72 AGUIARNOPOLIS 73 CHAPADAO DO CEU 74 BANDEIRANTES DO TOCANTINS 75 PEROLANDIA 76 BARRA DO OURO 77 CIDADE OCIDENTAL 78 CHAPADA DE AREIA 79 MONTIVIDIU DO NORTE 80 CHAPADA DA NATIVIDADE 81 CASTELANDIA 82 CRIXAS DO TOCANTINS 83 SANTO ANTONIO DA BARRA 84 IPUEIRAS 85 ALTO HORIZONTE 86 LAVANDEIRA 87 NOVA IGUACU DE GOIAS 88 LUZINOPOLIS 89 COTRIGUACU 90 MONTE SANTO DO TOCANTINS 91 PLANALTO DA SERRA 92 OLIVEIRA DE FATIMA 93 SAO PEDRO DA CIPA 94 PUGMIL 95 PONTAL DO ARAGUAIA 96 SANTA RITA DO TOCANTINS 97 QUERENCIA 98 SANTA TEREZINHA DO TOCANTINS 99 RIBEIRAOZINHO 100 TALISMA 101 PORTO ESTRELA 102 TUPIRAMA 103 NOVA MARILANDIA 104 AGUA DOCE DO MARANHAO 105 BRASILEIA 106 ALTO ALEGRE DO MARANHAO 107 CRUZEIRO DO SUL 108 ALTO ALEGRE DO PINDARE 109 MANCIO LIMA 110 AMAPA DO MARANHAO 111 NOVA MARINGA 112 APICUM-ACU 113 FEIJO 114 ARAGUANA 115 SANTO AFONSO 116 BACABEIRA 117 NOVA BANDEIRANTES 118 BACURITUBA 119 NOVA MONTE VERDE 120 BELAGUA 121 NOVA GUARITA 122 BELA VISTA DO MARANHAO 123 SANTA CARMEM 124 BERNARDO DO MEARIM 125 TABAPORA 126 BOA VISTA DO GURUPI 127 ALTO BOA VISTA 128 BOM JESUS DAS SELVAS 129 CANABRAVA DO NORTE 130 BOM LUGAR 131 CONFRESA 132 BREJO DE AREIA 133 SAO JOSE DO XINGU 134 BURITICUPU 135 GLORIA D'OESTE 136 BURITIRANA 137 LAMBARI D'OESTE 138 CACHOEIRA GRANDE 139 RIO BRANCO 140 CAMPESTRE DO MARANHAO 141 ALCINOPOLIS 142 CAPINZAL DO NORTE 143 NOVA ALVORADA DO SUL 144 CENTRAL DO MARANHAO 145 SENA MADUREIRA 146 CENTRO DO GUILHERME 147 TARAUACA 148 CENTRO NOVO DO MARANHAO 149 XAPURI 150 CIDELANDIA 151 PLACIDO DE CASTRO 152 CONCEICAO DO LAGO-ACU 153 SENADOR GUIOMARD 154 DAVINOPOLIS 155 MANOEL URBANO 156 FEIRA NOVA DO MARANHAO 157 ASSIS BRASIL 158 FERNANDO FALCAO 159 NOVO HORIZONTE DO SUL 160 FORMOSA DA SERRA NEGRA 161 JAPORA 162 GOVERNADOR EDISON LOBAO 163 LAGUNA CARAPA 164 GOVERNADOR LUIZ ROCHA 165 ANGICO 166 GOVERNADOR NEWTON BELLO 167 ARAGOMINAS 168 GOVERNADOR NUNES FREIRE 169 ARAGUANA 170 IGARAPE DO MEIO 171 CACHOEIRINHA 172 ITAIPAVA DO GRAJAU 173 CAMPOS LINDOS 174 ITINGA DO MARANHAO 175 CARMOLANDIA 176 JATOBA 177 CARRASCO BONITO 178 JENIPAPO DOS VIEIRAS 179 DARCINOPOLIS 180 JUNCO DO MARANHAO 181 ESPERANTINA 182 LAGOA DO MATO 183 MAURILANDIA DO TOCANTINS 184 LAGO DOS RODRIGUES 185 PALMEIRAS DO TOCANTINS 186 LAGOA GRANDE DO MARANHAO 187 MURICILANDIA 188 LAJEADO NOVO 189 PALMEIRANTE 190 MARACACUME 191 PAU D'ARCO 192 MARAJA DO SENA 193 RIACHINHO 194 MARANHAOZINHO 195 SANTA FE DO ARAGUAIA 196 MATOES DO NORTE 197 SAO BENTO DO TOCANTINS 198 MILAGRES DO MARANHAO 199 SAO MIGUEL DO TOCANTINS 200 NOVA COLINAS 201 NOVO AIRAO 202 NOVA OLINDA DO MARANHAO 203 ANORI 204 OLINDA NOVA DO MARANHAO 205 ATALAIA DO NORTE 206 PAULINO NEVES 207 AUTAZES 208 PEDRO DO ROSARIO 209 BARCELOS 210 PERITORO 211 BARREIRINHA 212 PORTO RICO DO MARANHAO 213 BENJAMIN CONSTANT 214 PRESIDENTE MEDICI 215 BOCA 

### 1.5 - Dados de Motivo de Situação


#### Carga

In [0]:

# path S3 no Tigris onde estão os dados de Empresas
s3_dir = "s3a://pos-pucrio-dados/mvp_sprint_eng_dados/mot/"

# os arquivos da RFB estão vindo sem header
# ler primeiro sem headers e acrescentar na mão depois
df_sem_headers = spark.read.option("delimiter", ";").option("encoding", "iso-8859-1").csv(s3_dir, header=False, inferSchema=True) 

# headers segundo doc (https://www.gov.br/receitafederal/dados/cnpj-metadados.pdf)
headers = ["codigo", "descricao"]

#df_sem_headers.show()
df = df_sem_headers.toDF(*headers) # acrescenta os headers no df original

In [0]:
# finalmente, carrega os dados em uma tabela Spark
df.write.option("encoding", "iso-8859-1").option("overwriteSchema", "true").mode("overwrite").saveAsTable("motivo_situacao")

In [0]:
%sql
-- verificando que inseriu corretamente, fazer select simples
select * from motivo_situacao

codigo descricao 0 SEM MOTIVO 1 EXTINCAO POR ENCERRAMENTO LIQUIDACAO VOLUNTARIA 2 INCORPORACAO 3 FUSAO 4 CISAO TOTAL 5 ENCERRAMENTO DA FALENCIA 6 ENCERRAMENTO DA LIQUIDACAO 7 ELEVACAO A MATRIZ 8 TRANSPASSE 9 NAO INICIO DE ATIVIDADE 10 EXTINCAO PELO ENCERRAMENTO DA LIQUIDACAO JUDICIAL 11 ANULACAO POR MULTICIPLIDADE 12 ANULACAO ONLINE DE OFICIO 13 OMISSA CONTUMAZ 14 OMISSA NAO LOCALIZADA 15 INEXISTENCIA DE FATO 16 ANULACAO POR VICIOS 17 BAIXA INICIADA EM ANALISE 18 INTERRUPCAO TEMPORARIA DAS ATIVIDADES 21 PEDIDO DE BAIXA INDEFERIDA 24 POR EMISSAO CERTIDAO NEGATIVA 28 TRANSFERENCIA FILIAL CONDICAO MATRIZ 31 EXTINCAO-UNIFICACAO DA FILIAL 33 TRANSFERENCIA DO ORGAO LOCAL A CONDICAO DE FILIAL DO ORGAO REGIONAL 34 ANULACAO DE INSCRICAO INDEVIDA 35 EMPRESA ESTRANGEIRA AGUARDANDO DOCUMENTACAO 36 PRATICA IRREGULAR DE OPERACAO DE COMERCIO EXTERIOR 37 BAIXA DE PRODUTOR RURAL 38 BAIXA DEFERIDA PELA RFB AGUARDANDO ANALISE DO CONVENENTE 39 BAIXA DEFERIDA PELA RFB E INDEFERIDA PELO CONVENENTE 40 BAIXA INDEFERIDA PELA RFB E AGUARDANDO ANALISE DO CONVENENTE 41 BAIXA INDEFERIDA PELA RFB E DEFERIDA PELO CONVENENTE 42 BAIXA DEFERIDA PELA RFB E SEFIN, AGUARDANDO ANALISE SEFAZ 43 BAIXA DEFERIDA PELA RFB, AGUARDANDO ANALISE DA SEFAZ E INDEFERIDA PELA SEFIN 44 BAIXA DEFERIDA PELA RFB E SEFAZ, AGUARDANDO ANALISE SEFIN 45 BAIXA DEFERIDA PELA RFB, AGUARDANDO ANALISE DA SEFIN E INDEFERIDA PELA SEFAZ 46 BAIXA DEFERIDA PELA RFB E SEFAZ E INDEFERIDA PELA SEFIN 47 BAIXA DEFERIDA PELA RFB E SEFIN E INDEFERIDA PELA SEFAZ 48 BAIXA INDEFERIDA PELA RFB, AGARDANDO ANALISE SEFAZ E DEFERIDA PELA SEFIN 49 BAIXA INDEFERIDA PELA RFB, AGUARDANDO ANALISE DA SEFAZ E INDEFERIDA PELA SEFIN 50 BAIXA INDEFERIDA PELA RFB, DEFERIDA PELA SEFAZ E AGUARDANDO ANALISE DA SEFIN 51 BAIXA INDEFERIDA PELA RFB E SEFAZ, AGUARDANDO ANALISE DA SEFIN 52 BAIXA INDEFERIDA PELA RFB, DEFERIDA PELA SEFAZ E INDEFERIDA PELA SEFIN 53 BAIXA INDEFERIDA PELA RFB E SEFAZ E DEFERIDA PELA SEFIN 54 EXTINCAO - TRATAMENTO DIFERENCIADO DADO AS ME E EPP (LEI COMPLEMENTAR NUMERO 123/2006) 55 DEFERIDO PELO CONVENENTE, AGUARDANDO ANALISE DA RFB 60 ARTIGO 30, VI, DA IN 748/2007 61 INDICIO INTERPOS. FRAUDULENTA 62 FALTA DE PLURALIDADE DE SOCIOS 63 OMISSAO DE DECLARACOES 64 LOCALIZACAO DESCONHECIDA 66 INAPTIDAO 67 REGISTRO CANCELADO 70 ANULACAO POR NAO CONFIRMADO ATO DE REGISTRO DO MEI NA JUNTA COMERCIAL 71 INAPTIDAO (LEI 11.941/2009 ART.54) 72 DETERMINACAO JUDICIAL 73 OMISSAO CONTUMAZ 74 INCONSISTENCIA CADASTRAL 75 OBITO DO MEI - TITULAR FALECIDO 80 BAIXA REGISTRADA NA JUNTA, INDEFERIDA NA RFB 82 SUSPENSO PERANTE A COMISSAO DE VALORES MOBILIARIOS - CVM

### 1.6 - Dados de Natureza Jurídica


#### Carga

In [0]:

# path S3 no Tigris onde estão os dados de Empresas
s3_dir = "s3a://pos-pucrio-dados/mvp_sprint_eng_dados/nat/"

# os arquivos da RFB estão vindo sem header
# ler primeiro sem headers e acrescentar na mão depois
df_sem_headers = spark.read.option("delimiter", ";").option("encoding", "iso-8859-1").csv(s3_dir, header=False, inferSchema=True) 

# headers segundo doc (https://www.gov.br/receitafederal/dados/cnpj-metadados.pdf)
headers = ["codigo", "descricao"]

#df_sem_headers.show()
df = df_sem_headers.toDF(*headers) # acrescenta os headers no df original

In [0]:
# finalmente, carrega os dados em uma tabela Spark
df.write.option("encoding", "iso-8859-1").option("overwriteSchema", "true").mode("overwrite").saveAsTable("natureza_juridica")

In [0]:
%sql
-- verificando que inseriu corretamente, fazer select simples
select * from natureza_juridica

codigo descricao 0 Natureza Jurídica não informada 3271 Órgão de Direção Local de Partido Político 3280 Comitê Financeiro de Partido Político 3298 Frente Plebiscitária ou Referendária 3301 Organização Social (OS) 3999 Associação Privada 4014 Empresa Individual Imobiliária 4090 Candidato a Cargo Político Eletivo 4120 Produtor Rural (Pessoa Física) 5010 Organização Internacional 5029 Representação Diplomática Estrangeira 1015 Órgão Público do Poder Executivo Federal 1023 Órgão Público do Poder Executivo Estadual ou do Distrito Federal 1031 Órgão Público do Poder Executivo Municipal 1040 Órgão Público do Poder Legislativo Federal 1058 Órgão Público do Poder Legislativo Estadual ou do Distrito Federal 1066 Órgão Público do Poder Legislativo Municipal 1074 Órgão Público do Poder Judiciário Federal 1082 Órgão Público do Poder Judiciário Estadual 1104 Autarquia Federal 1112 Autarquia Estadual ou do Distrito Federal 1120 Autarquia Municipal 1139 Fundação Pública de Direito Público Federal 1147 Fundação Pública de Direito Público Estadual ou do Distrito Federal 1155 Fundação Pública de Direito Público Municipal 1163 Órgão Público Autônomo Federal 1171 Órgão Público Autônomo Estadual ou do Distrito Federal 1180 Órgão Público Autônomo Municipal 1198 Comissão Polinacional 1210 Consórcio Público de Direito Público (Associação Pública) 1228 Consórcio Público de Direito Privado 1236 Estado ou Distrito Federal 1244 Município 1252 Fundação Pública de Direito Privado Federal 1260 Fundação Pública de Direito Privado Estadual ou do Distrito Federal 1279 Fundação Pública de Direito Privado Municipal 1287 Fundo Público da Administração Indireta Federal 1295 Fundo Público da Administração Indireta Estadual ou do Distrito Federal 1309 Fundo Público da Administração Indireta Municipal 1317 Fundo Público da Administração Direta Federal 1325 Fundo Público da Administração Direta Estadual ou do Distrito Federal 1333 Fundo Público da Administração Direta Municipal 1341 União 2011 Empresa Pública 2038 Sociedade de Economia Mista 2046 Sociedade Anônima Aberta 2054 Sociedade Anônima Fechada 2062 Sociedade Empresária Limitada 2070 Sociedade Empresária em Nome Coletivo 2089 Sociedade Empresária em Comandita Simples 2097 Sociedade Empresária em Comandita por Ações 2100 Sociedade Mercantil de Capital e Indústria 2127 Sociedade em Conta de Participação 2135 Empresário (Individual) 2143 Cooperativa 2151 Consórcio de Sociedades 2160 Grupo de Sociedades 2178 Estabelecimento, no Brasil, de Sociedade Estrangeira 2194 Estabelecimento, no Brasil, de Empresa Binacional Argentino-Brasileira 2216 Empresa Domiciliada no Exterior 2224 Clube/Fundo de Investimento 2232 Sociedade Simples Pura 2240 Sociedade Simples Limitada 2259 Sociedade Simples em Nome Coletivo 2267 Sociedade Simples em Comandita Simples 2275 Empresa Binacional 2283 Consórcio de Empregadores 2291 Consórcio Simples 2305 Empresa Individual de Responsabilidade Limitada (de Natureza Empresária) 2313 Empresa Individual de Responsabilidade Limitada (de Natureza Simples) 2321 Sociedade Unipessoal de Advocacia 2330 Cooperativas de Consumo 2348 Empresa Simples de Inovação 3034 Serviço Notarial e Registral (Cartório) 3069 Fundação Privada 3077 Serviço Social Autônomo 3085 Condomínio Edilício 3107 Comissão de Conciliação Prévia 3115 Entidade de Mediação e Arbitragem 3131 Entidade Sindical 3204 Estabelecimento, no Brasil, de Fundação ou Associação Estrangeiras 3212 Fundação ou Associação Domiciliada no Exterior 3220 Organização Religiosa 3239 Comunidade Indígena 3247 Fundo Privado 3255 Órgão de Direção Nacional de Partido Político 3263 Órgão de Direção Regional de Partido Político 5037 Outras Instituições Extraterritoriais 3328 Plano de Benefícios de Previdência Complementar Fechada 8885 Natureza Jurídica não informada

## 2 - Base dos Dados

### 2.1 - Municípios, Regiões Imediatas, Regiões Intermediárias (Base dos Dados / IBGE)

Para fazer análises regionalizadas, não restritas exclusivamente a um município alvo mas considerando também os municípios no entorno (região imediata e região intermediária, antigas micro e mesorregiões), podemos utilizar a base de DTB (Divisão Territorial) do IBGE. Entretanto, o código de município da RFB não é o mesmo do IBGE, que faria com que tivéssemos que fazer algum match por nome de município. Para contornar esta questão, vamos utilizar uma base já tratada, a base de Municípios na Base dos Dados (https://basedosdados.org/), site que agrega e trata dados de várias fontes brasileiras e traz o id da RFB e o do IBGE numa mesma tabela de municípios. 

Os dados da base de Municípios estão disponíveis como arquivos csv.gz no endereço abaixo:

https://basedosdados.org/dataset/33b49786-fb5f-496f-bb7c-9811c985af8e?table=dffb65ac-9df9-4151-94bf-88c45bfcb056

Os dados mais recentes disponíveis são os de set/2023.


#### Coleta / Extração

Apesar do pequeno tamanho, seguiremos o mesmo estilo utilizado para a base do QSA, i.e. baixar o zip localmente, processá-lo e subí-lo para um bucket S3 do Tigris, de onde o Spark lerá os dados e salvará numa Spark Table.

#### Carga


In [0]:

# path S3 no Tigris onde estão os dados de Empresas
s3_dir = "s3a://pos-pucrio-dados/mvp_sprint_eng_dados/mun-bd/"

# os arquivos da BD já vem com headers, então só ler
df = spark.read.option("delimiter", ",").csv(s3_dir, header=True, inferSchema=True) 

In [0]:
# finalmente, carrega os dados em uma tabela Spark
df.write.mode("overwrite").saveAsTable("municipio_bd")

In [0]:
%sql
-- verificando que inseriu corretamente, fazer select simples
select * from municipio_bd

id_municipio id_municipio_6 id_municipio_tse id_municipio_rf id_municipio_bcb nome capital_uf id_comarca id_regiao_saude nome_regiao_saude id_regiao_imediata nome_regiao_imediata id_regiao_intermediaria nome_regiao_intermediaria id_microrregiao nome_microrregiao id_mesorregiao nome_mesorregiao id_regiao_metropolitana nome_regiao_metropolitana ddd id_uf sigla_uf nome_uf nome_regiao amazonia_legal centroide 1100338 110033 434 47 44516 Nova Mamoré 0 1100106 11004 Madeira-Mamoré 110001 Porto Velho 1101 Porto Velho 11001 Porto Velho 1101 Madeira-Guaporé null null 69 11 RO Rondônia Norte 1 POINT(-64.6295025002404 -10.3822863210755) 1100205 110020 35 3 30719 Porto Velho 1 1100205 11004 Madeira-Mamoré 110001 Porto Velho 1101 Porto Velho 11001 Porto Velho 1101 Madeira-Guaporé 101 Região Metropolitana de Porto Velho 69 11 RO Rondônia Norte 1 POINT(-64.3041357999869 -9.15394033687075) 1101104 110110 493 683 46851 Itapuã do Oeste 0 1100205 11004 Madeira-Mamoré 110001 Porto Velho 1101 Porto Velho 11001 Porto Velho 1101 Madeira-Guaporé null null 69 11 RO Rondônia Norte 1 POINT(-63.044960463046 -9.17019402601564) 1100809 110080 477 681 46961 Candeias do Jamari 0 1100205 11004 Madeira-Mamoré 110001 Porto Velho 1101 Porto Velho 11001 Porto Velho 1101 Madeira-Guaporé 101 Região Metropolitana de Porto Velho 69 11 RO Rondônia Norte 1 POINT(-63.3254198532114 -8.88702392955617) 1100940 110094 680 8 56652 Cujubim 0 1100023 11001 Vale do Jamari 110002 Ariquemes 1101 Porto Velho 11001 Porto Velho 1101 Madeira-Guaporé null null 69 11 RO Rondônia Norte 1 POINT(-62.5652673033848 -9.1709863446154) 1100452 110045 779 4 56638 Buritis 0 1100452 11001 Vale do Jamari 110002 Ariquemes 1101 Porto Velho 11001 Porto Velho 1101 Madeira-Guaporé null null 69 11 RO Rondônia Norte 1 POINT(-63.9412277150937 -10.052095567536) 1100700 110070 671 679 46947 Campo Novo de Rondônia 0 1100452 11001 Vale do Jamari 110002 Ariquemes 1101 Porto Velho 11001 Porto Velho 1101 Madeira-Guaporé null null 69 11 RO Rondônia Norte 1 POINT(-63.7997903925811 -10.484878565906) 1100106 110010 19 1 22882 Guajará-Mirim 0 1100106 11004 Madeira-Mamoré 110001 Porto Velho 1101 Porto Velho 11002 Guajará-Mirim 1101 Madeira-Guaporé null null 69 11 RO Rondônia Norte 1 POINT(-64.537710733004 -11.3055098790143) 1100080 110008 213 21 41117 Costa Marques 0 1100080 11007 Vale do Guaporé 110004 Ji-Paraná 1102 Ji-Paraná 11002 Guajará-Mirim 1101 Madeira-Guaporé null null 69 11 RO Rondônia Norte 1 POINT(-64.0586026986492 -12.1470859394294) 1101492 110149 795 20 56717 São Francisco do Guaporé 0 1101492 11007 Vale do Guaporé 110004 Ji-Paraná 1102 Ji-Paraná 11002 Guajará-Mirim 1101 Madeira-Guaporé null null 69 11 RO Rondônia Norte 1 POINT(-63.1226712699562 -12.3688265389959) 1101401 110140 663 685 46507 Monte Negro 0 1100023 11001 Vale do Jamari 110002 Ariquemes 1101 Porto Velho 11003 Ariquemes 1102 Leste Rondoniense null null 69 11 RO Rondônia Norte 1 POINT(-63.3724143382525 -10.2109441112104) 1100601 110060 620 677 46978 Cacaulândia 0 1100023 11001 Vale do Jamari 110002 Ariquemes 1101 Porto Velho 11003 Ariquemes 1102 Leste Rondoniense null null 69 11 RO Rondônia Norte 1 POINT(-62.9872365107648 -10.3316252433648) 1100403 110040 639 675 46909 Alto Paraíso 0 1100023 11001 Vale do Jamari 110002 Ariquemes 1101 Porto Velho 11003 Ariquemes 1102 Leste Rondoniense null null 69 11 RO Rondônia Norte 1 POINT(-63.3941889058133 -9.64949873236446) 1100023 110002 78 7 9393 Ariquemes 0 1100023 11001 Vale do Jamari 110002 Ariquemes 1101 Porto Velho 11003 Ariquemes 1102 Leste Rondoniense null null 69 11 RO Rondônia Norte 1 POINT(-62.9572500386403 -9.95200191172898) 1100262 110026 647 687 46916 Rio Crespo 0 1100023 11001 Vale do Jamari 110002 Ariquemes 1101 Porto Velho 11003 Ariquemes 1102 Leste Rondoniense null null 69 11 RO Rondônia Norte 1 POINT(-62.7900702016081 -9.64518849498086) 1101757 110175 698 24 56731 Vale do Anari 0 1100130 11003 Central 110003 Jaru 1101 Porto Velho 11003 Ariquemes 1102 Leste Rondoniense null null 69 11 

### 2.2 - CNAEs (Base dos Dados / IBGE)

A classificação de CNAEs em si é organizada de forma hierárquica, mas a base apresentada pela RFB não traz os níveis intermediários de Divisão, Grupo ou Classe, que seriam úteis para uma análise ou busca em nível mais agregado. Para suprir esse gap, vamos utilizar uma base já tratada, a base de CNAEs na Base dos Dados (https://basedosdados.org/), site que agrega e trata dados de várias fontes brasileiras e traz esta base de CNAEs do IBGE com estas dimensões de níveis agregados já computadas para cada CNAE. 

Os dados da base de CNAEs estão disponíveis como arquivos csv.gz no endereço abaixo:

https://basedosdados.org/dataset/33b49786-fb5f-496f-bb7c-9811c985af8e?table=8a02c4e5-1718-41e7-8891-d0fa09265d58


Os dados mais recentes disponíveis são os de ago/2024.



#### Coleta / Extração

Apesar do pequeno tamanho, seguiremos o mesmo estilo utilizado para a base do QSA, i.e. baixar o zip localmente, processá-lo e subí-lo para um bucket S3 do Tigris, de onde o Spark lerá os dados e salvará numa Spark Table.

#### Carga


In [0]:

# path S3 no Tigris onde estão os dados de Empresas
s3_dir = "s3a://pos-pucrio-dados/mvp_sprint_eng_dados/cnae-bd/"

# os arquivos da BD já vem com headers, então só ler
# apenas um cuidado: alguns registros estão espalhados por mais de 1 linha de cada vez - habilitar opção de multiline
df = spark.read.option("delimiter", ",").option("multiLine", "true").csv(s3_dir, header=True, inferSchema=True) 

In [0]:
# finalmente, carrega os dados em uma tabela Spark
df.write.mode("overwrite").saveAsTable("cnae_bd")

In [0]:
%sql
-- verificando que inseriu corretamente, fazer select simples
select * from cnae_bd

subclasse descricao_subclasse classe descricao_classe grupo descricao_grupo divisao descricao_divisao secao descricao_secao indicador_cnae_2_0 indicador_cnae_2_1 indicador_cnae_2_2 indicador_cnae_2_3 9700500 Serviços domésticos 97005 Serviços domésticos 970 Serviços domésticos 97 Serviços Domésticos T Serviços Domésticos 1 1 1 1 9900800 Organismos internacionais e outras instituições extraterritoriais 99008 Organismos internacionais e outras instituições extraterritoriais 990 Organismos internacionais e outras instituições extraterritoriais 99 Organismos Internacionais E Outras Instituições Extraterritoriais U Organismos Internacionais E Outras Instituições Extraterritoriais 1 1 1 0 111301 Cultivo de arroz 1113 Cultivo de cereais 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 111399 Cultivo de outros cereais não especificados anteriormente 1113 Cultivo de cereais 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 111302 Cultivo de milho 1113 Cultivo de cereais 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 111303 Cultivo de trigo 1113 Cultivo de cereais 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 112102 Cultivo de juta 1121 Cultivo de algodão herbáceo e de outras fibras de lavoura temporária 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 112101 Cultivo de algodão herbáceo 1121 Cultivo de algodão herbáceo e de outras fibras de lavoura temporária 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 112199 Cultivo de outras fibras de lavoura temporária não especificadas anteriormente 1121 Cultivo de algodão herbáceo e de outras fibras de lavoura temporária 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 113000 Cultivo de cana-de-açúcar 1130 Cultivo de cana-de-açúcar 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 114800 Cultivo de fumo 1148 Cultivo de fumo 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 115600 Cultivo de soja 1156 Cultivo de soja 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 116402 Cultivo de girassol 1164 Cultivo de oleaginosas de lavoura temporária, exceto soja 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 116499 Cultivo de outras oleaginosas de lavoura temporária não especificadas anteriormente 1164 Cultivo de oleaginosas de lavoura temporária, exceto soja 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 116403 Cultivo de mamona 1164 Cultivo de oleaginosas de lavoura temporária, exceto soja 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricultura, Pecuária, Produção Florestal, Pesca E Aquicultura 1 1 1 1 116401 Cultivo de amendoim 1164 Cultivo de oleaginosas de lavoura temporária, exceto soja 11 Produção de lavouras temporárias 1 Agricultura, Pecuária E Serviços Relacionados A Agricult